In [1]:
import math
import torch
import pickle
import torch.cuda
import torchvision.transforms as transforms
import torch.utils.data as data
import torchvision.datasets as dsets
import os
from utils.BBBConvmodel import BBBAlexNet, BBBLeNet, BBB3Conv3FC, BBBVGG16
from utils.BBBlayers import GaussianVariationalInference
import numpy as np
from scipy.stats import norm
cuda = torch.cuda.is_available()
import pandas as pd
from matplotlib import pyplot as plt
import scipy

In [2]:
batch_size = 32
lr = 0.001
dataset = 'CIFAR-10'
network = 'lenet'
epoch = 50
if epoch != 50:
    model = torch.load("../results/{}_b{}_lr{}epoch{}_{}.pth".format(network, batch_size, lr, epoch, dataset))
else:
    model = torch.load("../results/{}_b{}_lr{}_{}.pth".format(network, batch_size, lr, dataset))
net = BBBLeNet
num_samples = 10
beta_type = "Blundell"

In [3]:
# dimensions of input and output
if dataset == 'MNIST':    # train with MNIST
    outputs = 10
    inputs = 1
elif dataset == 'CIFAR-10':  # train with CIFAR-10
    outputs = 10
    inputs = 3
elif dataset == 'CIFAR-100':    # train with CIFAR-100
    outputs = 100
    inputs = 3

if net == BBBLeNet or BBB3Conv3FC:
    resize = 32
elif net == BBBAlexNet:
    resize = 227

In [4]:
'''
LOADING DATASET
'''

if dataset == 'MNIST':
    transform = transforms.Compose([transforms.Resize((resize, resize)), transforms.ToTensor(),
                                    transforms.Normalize((0.1307,), (0.3081,))])
    train_dataset = dsets.MNIST(root="data", download=True, transform=transform)
    val_dataset = dsets.MNIST(root="data", download=True, train=False, transform=transform)

elif dataset == 'CIFAR-100':
    transform = transforms.Compose([transforms.Resize((resize, resize)), transforms.ToTensor(),
                                    transforms.Normalize((0.485, 0.456, 0.406), (0.229, 0.224, 0.225))])
    train_dataset = dsets.CIFAR100(root="data", download=True, transform=transform)
    val_dataset = dsets.CIFAR100(root='data', download=True, train=False, transform=transform)

elif dataset == 'CIFAR-10':
    transform = transforms.Compose([transforms.Resize((resize, resize)), transforms.ToTensor(),
                                    transforms.Normalize((0.485, 0.456, 0.406), (0.229, 0.224, 0.225))])
    train_dataset = dsets.CIFAR10(root="data", download=True, transform=transform)
    val_dataset = dsets.CIFAR10(root='data', download=True, train=False, transform=transform)

Files already downloaded and verified
Files already downloaded and verified


In [5]:
loader_val = data.DataLoader(dataset=val_dataset, batch_size=batch_size, shuffle=False)

In [6]:
model.state_dict().keys()

odict_keys(['conv1.qw_mean', 'conv1.qw_logvar', 'conv1.qb_mean', 'conv1.qb_logvar', 'conv1.conv_qw_mean', 'conv1.conv_qw_si', 'conv1.log_alpha', 'conv2.qw_mean', 'conv2.qw_logvar', 'conv2.qb_mean', 'conv2.qb_logvar', 'conv2.conv_qw_mean', 'conv2.conv_qw_si', 'conv2.log_alpha', 'fc1.qw_mean', 'fc1.qw_logvar', 'fc1.qb_mean', 'fc1.qb_logvar', 'fc1.fc_qw_mean', 'fc1.fc_qw_si', 'fc1.log_alpha', 'fc2.qw_mean', 'fc2.qw_logvar', 'fc2.qb_mean', 'fc2.qb_logvar', 'fc2.fc_qw_mean', 'fc2.fc_qw_si', 'fc2.log_alpha', 'fc3.qw_mean', 'fc3.qw_logvar', 'fc3.qb_mean', 'fc3.qb_logvar', 'fc3.fc_qw_mean', 'fc3.fc_qw_si', 'fc3.log_alpha', 'layers.0.qw_mean', 'layers.0.qw_logvar', 'layers.0.qb_mean', 'layers.0.qb_logvar', 'layers.0.conv_qw_mean', 'layers.0.conv_qw_si', 'layers.0.log_alpha', 'layers.3.qw_mean', 'layers.3.qw_logvar', 'layers.3.qb_mean', 'layers.3.qb_logvar', 'layers.3.conv_qw_mean', 'layers.3.conv_qw_si', 'layers.3.log_alpha', 'layers.7.qw_mean', 'layers.7.qw_logvar', 'layers.7.qb_mean', 'layers

# 合并weights

In [7]:
if network == "lenet":
    w_name = ['layers.0.qw_', 'layers.3.qw_', 'layers.7.qw_','layers.9.qw_', 'layers.11.qw_']
    b_name = ['layers.0.qb_', 'layers.3.qb_', 'layers.7.qb_','layers.9.qb_', 'layers.11.qb_']
elif network == "vgg16":
    w_name = ['layers.0.qw_', 'layers.2.qw_', 'layers.4.qw_','layers.6.qw_', 'layers.8.qw_', 
              'layers.10.qw_', 'layers.12.qw_', 'layers.14.qw_', 'layers.16.qw_', 'layers.18.qw_',
            'layers.20.qw_', 'layers.22.qw_', 'layers.24.qw_', 'layers.27.qw_', 'layers.30.qw_', 'layers.33.qw_']
    b_name = ['layers.0.qb_', 'layers.2.qb_', 'layers.4.qb_','layers.6.qb_', 'layers.8.qb_', 
              'layers.10.qb_', 'layers.12.qb_', 'layers.14.qb_', 'layers.16.qb_', 'layers.18.qb_',
            'layers.20.qb_', 'layers.22.qb_', 'layers.24.qb_', 'layers.27.qb_', 'layers.30.qb_', 'layers.33.qb_']

In [8]:
model = model.cpu()

In [9]:
whole_w = []
for (i, j) in zip(w_name, b_name):
    whole_w.append(model.state_dict()['{}mean'.format(i)].numpy().ravel())
    whole_w.append(model.state_dict()['{}mean'.format(j)].numpy().ravel())
whole_w = np.concatenate(whole_w)

In [10]:
len(whole_w)

62006

In [11]:
len(whole_w[np.abs(whole_w) <= 1e-2])

7562

# 神经网络精度计算函数

In [14]:
vi = GaussianVariationalInference(torch.nn.CrossEntropyLoss())

def run_epoch(loader, epoch, is_training=False, model=model):
    m = math.ceil(len(loader.dataset) / loader.batch_size)

    accuracies = []
    likelihoods = []
    kls = []
    losses = []

    for i, (images, labels) in enumerate(loader):
        # # Repeat samples (Casper's trick)
        # x = images.view(-1, inputs, resize, resize).repeat(num_samples, 1, 1, 1)
        # y = labels.repeat(num_samples)
        x = images.view(-1, inputs, resize, resize)
        y = labels
        if cuda:
            x = x.cuda()
            y = y.cuda()

        if beta_type == "Blundell":
            beta = 2 ** (m - (i + 1)) / (2 ** m - 1)
        elif beta_type == "Soenderby":
            beta = min(epoch / (num_epochs//4), 1)
        elif beta_type == "Standard":
            beta = 1 / m
        else:
            beta = 0

        logits, kl = model.probforward(x)
        loss = vi(logits, y, kl, beta)
        ll = -loss.data.mean() + beta*kl.data.mean()

        if is_training:
            optimiser.zero_grad()
            loss.backward()
            optimiser.step()

        _, predicted = logits.max(1)
        accuracy = (predicted.data.cpu() == y.cpu()).float().mean()

        accuracies.append(accuracy)
        losses.append(loss.data.mean())
        kls.append(beta*kl.data.mean())
        likelihoods.append(ll)

    diagnostics = {'loss': sum(losses)/len(losses),
                   'acc': sum(accuracies)/len(accuracies),
                   'kl': sum(kls)/len(kls),
                   'likelihood': sum(likelihoods)/len(likelihoods)}

    return diagnostics

In [15]:
model = model.cuda()
diagnostics_val = run_epoch(loader_val, epoch=1)

logits tensor([[-2.3721e+00, -3.6252e+00,  4.2061e-01,  3.2041e+00, -1.8782e+00,
          3.1503e+00,  1.4898e+00, -3.7204e-01, -1.9544e-01, -3.2769e+00],
        [ 3.9334e+00,  4.3990e+00, -2.3246e+00, -5.0156e+00, -3.9455e+00,
         -5.3870e+00, -5.7886e+00, -5.8502e+00,  7.1570e+00,  1.3283e+00],
        [ 2.3102e+00,  2.0154e+00, -1.8554e+00, -2.2365e+00, -3.2544e+00,
         -2.5123e+00, -4.5370e+00, -2.0025e+00,  3.2139e+00,  1.3298e+00],
        [ 4.6018e+00, -1.7789e-01,  1.9427e+00, -1.7259e+00, -1.5869e+00,
         -3.4990e+00, -3.0108e+00, -5.6221e+00,  4.4678e+00, -1.8816e+00],
        [-3.9517e+00, -3.2634e+00,  1.1042e+00,  1.5557e+00,  3.3815e+00,
          1.2962e+00,  2.1697e+00, -1.0725e+00, -3.9768e+00, -3.1550e+00],
        [-1.5996e+00, -4.3839e+00,  1.0081e+00,  1.1116e+00,  1.1007e-01,
          1.2043e+00,  3.6121e+00,  1.2593e-01, -5.2894e+00, -3.2879e+00],
        [ 1.2914e+00,  2.8256e+00,  8.3045e-01,  9.9380e-01, -4.1298e+00,
          8.8518e-01, -1.

In [16]:
diagnostics_val

{'loss': tensor(310.4900, device='cuda:0'),
 'acc': tensor(0.6022),
 'kl': tensor(309.3527, device='cuda:0'),
 'likelihood': tensor(-1.1372, device='cuda:0')}

In [18]:
def evaluate(loader, epoch=1):
    m = math.ceil(len(loader.dataset) / loader.batch_size)

    accuracies = []

    for i, (images, labels) in enumerate(loader):
        # # Repeat samples (Casper's trick)
        # x = images.view(-1, inputs, resize, resize).repeat(num_samples, 1, 1, 1)
        # y = labels.repeat(num_samples)

        x = images.view(-1, inputs, resize, resize)
        y = labels

        if cuda:
            x = x.cuda()
            y = y.cuda()

        logits = cpr_model(x)
        _, predicted = torch.max(logits.data, 1)
        accuracy = (predicted.data.cpu() == y.cpu()).float().mean()

        accuracies.append(accuracy)

    diagnostics = {'acc': sum(accuracies)/len(accuracies)}

    return diagnostics

把BNN的weights套进确定性网络，测试精度

In [19]:
uncompressed_list = []
for (i, j) in zip(w_name, b_name):
    # w
    vecs_u1 = model.state_dict()['{}mean'.format(i)]
    uncompressed_list.append(vecs_u1)
    # b
    vecs_u2 = model.state_dict()['{}mean'.format(j)]
    uncompressed_list.append(vecs_u2)

if network == "lenet":
    # lenet
    from model import lenet
    cpr_model=lenet(inputs)
elif network == "vgg16":
    from model import VGG16
    cpr_model = VGG16(inputs)
name_uncpr=cpr_model.state_dict().keys()
uncpr_state_dict = dict(zip(name_uncpr, uncompressed_list))
cpr_model.load_state_dict(uncpr_state_dict)
# 用压缩后的模型计算loss，acc等
cpr_model = cpr_model.cuda()
diagnostics_uncpr_val = evaluate(loader_val)

In [20]:
diagnostics_uncpr_val

{'acc': tensor(0.5853)}

# all layers放在一起压缩

In [21]:
def compress_coordinates(means, stds, beta, bitlengths):
    # N = len(means.ravel()) = len(stds.ravel())
    # C = len(codepoints)
    optima = np.empty_like(means)
    optima_lengths = np.empty_like(means, dtype=int)
    for i in range(0, 10000000, 100000):
        if i % 100000 == 0:
            print(i / 1000000)
        squared_errors = (codepoints[np.newaxis, :] - means.ravel()[i:i+100000, np.newaxis])**2
            # shape (N, C)
        weighted_penalties = (2 * beta) * stds.ravel()[i:i+100000, np.newaxis]**2 * bitlengths[np.newaxis, :]
            # shape (N, C)
        optima_idxs = np.argmin(squared_errors + weighted_penalties, axis=1)
        optima.ravel()[i:i+100000] = codepoints[optima_idxs]
        optima_lengths.ravel()[i:i+100000] = bitlengths[optima_idxs]
    return optima, optima_lengths

In [22]:
model = model.cpu()

In [23]:
results = [['full', 'full', diagnostics_val['acc'].numpy(), 'None']]
compressed_len_list = []
betas = [0.0001, 0.001, 0.01, 0.1, 1, 10, 100]
bitlengths = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
# betas = [0.01]
# bitlengths = [2]

empirical_mean = np.mean(whole_w)
empirical_std = np.std(whole_w)

for max_codepoint_length in bitlengths:
    for beta_ in betas:
        compressed_len = 0
        compressed_list = []
        for (i, j) in zip(w_name, b_name):
            codepoints_and_lengths = [
                (scipy.stats.norm.ppf(codepoint_xi, loc=empirical_mean, scale=empirical_std), length)
                for length in range(max_codepoint_length+1)
                for codepoint_xi in np.arange(0.5**(length+1), 1, 0.5**length)
            ]
            codepoints = np.array([codepoint for codepoint, _ in codepoints_and_lengths])
            lengths = np.array([length for _, length in codepoints_and_lengths])
            # compress w
            vecs_u1 = model.state_dict()['{}mean'.format(i)].numpy()
            stds_u1 = np.exp(model.state_dict()['{}logvar'.format(i)].numpy())
            compressed1, cpr_len1 = compress_coordinates(vecs_u1,stds_u1,beta_,lengths)
            compressed1 = torch.from_numpy(compressed1)
            compressed_list.append(compressed1)
            compressed_len += np.sum(cpr_len1)
            # compress b
            vecs_u2 = model.state_dict()['{}mean'.format(j)].numpy()
            stds_u2 = np.exp(model.state_dict()['{}logvar'.format(j)].numpy())
            compressed2, cpr_len2 = compress_coordinates(vecs_u2,stds_u2,beta_,lengths)
            compressed2 = torch.from_numpy(compressed2)
            compressed_list.append(compressed2)
            compressed_len += np.sum(cpr_len2)

        compressed_len_list.append([max_codepoint_length, beta_, compressed_len, 'global'])
        
        if network == "lenet":
            # lenet
            from model import lenet
            cpr_model=lenet(inputs)
        elif network == "vgg16":
            from model import VGG16
            cpr_model = VGG16(inputs)
        print(max_codepoint_length, beta_)
        name_cpr=cpr_model.state_dict().keys()
        cpr_state_dict = dict(zip(name_cpr, compressed_list))
        cpr_model.load_state_dict(cpr_state_dict)
        # 用压缩后的模型计算loss，acc等
        cpr_model = cpr_model.cuda()
        diagnostics_cpr_val = evaluate(loader_val)
        results.append([max_codepoint_length, beta_, diagnostics_cpr_val['acc'].numpy(), 'global'])

0.0
0.1
0.2
0.3
0.4
0.5
0.6
0.7
0.8
0.9
1.0
1.1
1.2
1.3
1.4
1.5
1.6
1.7
1.8
1.9
2.0
2.1
2.2
2.3
2.4
2.5
2.6
2.7
2.8
2.9
3.0
3.1
3.2
3.3
3.4
3.5
3.6
3.7
3.8
3.9
4.0
4.1
4.2
4.3
4.4
4.5
4.6
4.7
4.8
4.9
5.0
5.1
5.2
5.3
5.4
5.5
5.6
5.7
5.8
5.9
6.0
6.1
6.2
6.3
6.4
6.5
6.6
6.7
6.8
6.9
7.0
7.1
7.2
7.3
7.4
7.5
7.6
7.7
7.8
7.9
8.0
8.1
8.2
8.3
8.4
8.5
8.6
8.7
8.8
8.9
9.0
9.1
9.2
9.3
9.4
9.5
9.6
9.7
9.8
9.9
0.0
0.1
0.2
0.3
0.4
0.5
0.6
0.7
0.8
0.9
1.0
1.1
1.2
1.3
1.4
1.5
1.6
1.7
1.8
1.9
2.0
2.1
2.2
2.3
2.4
2.5
2.6
2.7
2.8
2.9
3.0
3.1
3.2
3.3
3.4
3.5
3.6
3.7
3.8
3.9
4.0
4.1
4.2
4.3
4.4
4.5
4.6
4.7
4.8
4.9
5.0
5.1
5.2
5.3
5.4
5.5
5.6
5.7
5.8
5.9
6.0
6.1
6.2
6.3
6.4
6.5
6.6
6.7
6.8
6.9
7.0
7.1
7.2
7.3
7.4
7.5
7.6
7.7
7.8
7.9
8.0
8.1
8.2
8.3
8.4
8.5
8.6
8.7
8.8
8.9
9.0
9.1
9.2
9.3
9.4
9.5
9.6
9.7
9.8
9.9
0.0
0.1
0.2
0.3
0.4
0.5
0.6
0.7
0.8
0.9
1.0
1.1
1.2
1.3
1.4
1.5
1.6
1.7
1.8
1.9
2.0
2.1
2.2
2.3
2.4
2.5
2.6
2.7
2.8
2.9
3.0
3.1
3.2
3.3
3.4
3.5
3.6
3.7
3.8
3.9
4.0
4.1
4.2
4.3
4.4
4.5
4.6
4.7
4.8
4.9


In [24]:
results

[['full', 'full', array(0.60223645, dtype=float32), 'None'],
 [1, 0.0001, array(0.12809505, dtype=float32), 'global'],
 [1, 0.001, array(0.12220448, dtype=float32), 'global'],
 [1, 0.01, array(0.13128993, dtype=float32), 'global'],
 [1, 0.1, array(0.09984025, dtype=float32), 'global'],
 [1, 1, array(0.10013977, dtype=float32), 'global'],
 [1, 10, array(0.10013977, dtype=float32), 'global'],
 [1, 100, array(0.09984025, dtype=float32), 'global'],
 [2, 0.0001, array(0.26347843, dtype=float32), 'global'],
 [2, 0.001, array(0.25758785, dtype=float32), 'global'],
 [2, 0.01, array(0.22823483, dtype=float32), 'global'],
 [2, 0.1, array(0.09984025, dtype=float32), 'global'],
 [2, 1, array(0.10013977, dtype=float32), 'global'],
 [2, 10, array(0.10013977, dtype=float32), 'global'],
 [2, 100, array(0.09984025, dtype=float32), 'global'],
 [3, 0.0001, array(0.32208467, dtype=float32), 'global'],
 [3, 0.001, array(0.3154952, dtype=float32), 'global'],
 [3, 0.01, array(0.30361423, dtype=float32), 'glo

# 每层用不同P(z)

In [26]:
for max_codepoint_length in bitlengths:
    for beta_ in betas:
        compressed_len = 0
        compressed_list = []
        for (i, j) in zip(w_name, b_name):
            # w
            vecs_u1 = model.state_dict()['{}mean'.format(i)].numpy()
            stds_u1 = np.exp(model.state_dict()['{}logvar'.format(i)].numpy())
            # b
            vecs_u2 = model.state_dict()['{}mean'.format(j)].numpy()
            stds_u2 = np.exp(model.state_dict()['{}logvar'.format(j)].numpy())
            # 先把w和b合并在一起再拟合高斯
            vecs_u = np.concatenate([vecs_u1.ravel(), vecs_u2.ravel()])

            empirical_mean = np.mean(vecs_u)
            empirical_std = np.std(vecs_u)
            codepoints_and_lengths = [
                (scipy.stats.norm.ppf(codepoint_xi, loc=empirical_mean, scale=empirical_std), length)
                for length in range(max_codepoint_length+1)
                for codepoint_xi in np.arange(0.5**(length+1), 1, 0.5**length)
            ]
            codepoints = np.array([codepoint for codepoint, _ in codepoints_and_lengths])
            lengths = np.array([length for _, length in codepoints_and_lengths])

            compressed1, cpr_len1 = compress_coordinates(vecs_u1,stds_u1,beta_,lengths)
            compressed1 = torch.from_numpy(compressed1)
            compressed_list.append(compressed1)
            compressed_len += np.sum(cpr_len1)
            # compress b
            compressed2, cpr_len2 = compress_coordinates(vecs_u2,stds_u2,beta_,lengths)
            compressed2 = torch.from_numpy(compressed2)
            compressed_list.append(compressed2)
            compressed_len += np.sum(cpr_len2)

        compressed_len_list.append([max_codepoint_length, beta_, compressed_len, 'layer-wise'])
        # lenet
        from model import lenet
        cpr_model=lenet(inputs)
        print(max_codepoint_length, beta_)
        print(compressed_list)
        name_cpr=cpr_model.state_dict().keys()
        cpr_state_dict = dict(zip(name_cpr, compressed_list))
        cpr_model.load_state_dict(cpr_state_dict)
        cpr_model = cpr_model.cuda()
        # 用压缩后的模型计算loss，acc等
        diagnostics_cpr_val = evaluate(loader_val)
        results.append([max_codepoint_length, beta_, diagnostics_cpr_val['acc'].numpy(), 'layer-wise'])

0.0
0.1
0.2
0.3
0.4
0.5
0.6
0.7
0.8
0.9
1.0
1.1
1.2
1.3
1.4
1.5
1.6
1.7
1.8
1.9
2.0
2.1
2.2
2.3
2.4
2.5
2.6
2.7
2.8
2.9
3.0
3.1
3.2
3.3
3.4
3.5
3.6
3.7
3.8
3.9
4.0
4.1
4.2
4.3
4.4
4.5
4.6
4.7
4.8
4.9
5.0
5.1
5.2
5.3
5.4
5.5
5.6
5.7
5.8
5.9
6.0
6.1
6.2
6.3
6.4
6.5
6.6
6.7
6.8
6.9
7.0
7.1
7.2
7.3
7.4
7.5
7.6
7.7
7.8
7.9
8.0
8.1
8.2
8.3
8.4
8.5
8.6
8.7
8.8
8.9
9.0
9.1
9.2
9.3
9.4
9.5
9.6
9.7
9.8
9.9
0.0
0.1
0.2
0.3
0.4
0.5
0.6
0.7
0.8
0.9
1.0
1.1
1.2
1.3
1.4
1.5
1.6
1.7
1.8
1.9
2.0
2.1
2.2
2.3
2.4
2.5
2.6
2.7
2.8
2.9
3.0
3.1
3.2
3.3
3.4
3.5
3.6
3.7
3.8
3.9
4.0
4.1
4.2
4.3
4.4
4.5
4.6
4.7
4.8
4.9
5.0
5.1
5.2
5.3
5.4
5.5
5.6
5.7
5.8
5.9
6.0
6.1
6.2
6.3
6.4
6.5
6.6
6.7
6.8
6.9
7.0
7.1
7.2
7.3
7.4
7.5
7.6
7.7
7.8
7.9
8.0
8.1
8.2
8.3
8.4
8.5
8.6
8.7
8.8
8.9
9.0
9.1
9.2
9.3
9.4
9.5
9.6
9.7
9.8
9.9
0.0
0.1
0.2
0.3
0.4
0.5
0.6
0.7
0.8
0.9
1.0
1.1
1.2
1.3
1.4
1.5
1.6
1.7
1.8
1.9
2.0
2.1
2.2
2.3
2.4
2.5
2.6
2.7
2.8
2.9
3.0
3.1
3.2
3.3
3.4
3.5
3.6
3.7
3.8
3.9
4.0
4.1
4.2
4.3
4.4
4.5
4.6
4.7
4.8
4.9


In [27]:
results = pd.DataFrame(results)
results.columns = ['bitlength', 'beta', 'acc_test', 'method']

In [28]:
results

bitlength    beta     acc_test      method
0        full    full   0.60223645        None
1           1  0.0001   0.12809505      global
2           1   0.001  0.122204475      global
3           1    0.01   0.13128993      global
4           1     0.1   0.09984025      global
..        ...     ...          ...         ...
136        10    0.01   0.48801917  layer-wise
137        10     0.1   0.09984025  layer-wise
138        10       1   0.09984025  layer-wise
139        10      10   0.09984025  layer-wise
140        10     100  0.100139774  layer-wise

[141 rows x 4 columns]

In [30]:
results.to_csv("../results/lenet_withbias_b{}_lr{}_{}_gaussian.csv".format(batch_size, lr, dataset), index=False)

In [63]:
cpr_len_df = pd.DataFrame(compressed_len_list)
cpr_len_df.columns = ['bitlength', 'beta', 'len', 'method']
cpr_len_df['len'] = cpr_len_df['len'] / whole_w.size

In [64]:
cpr_len_df

bitlength      beta       len      method
0            1    0.0001  0.656920      global
1            1    0.0010  0.656904      global
2            1    0.0100  0.656872      global
3            1    0.1000  0.656582      global
4            1    1.0000  0.652888      global
..         ...       ...       ...         ...
135         10    0.0100  5.246912  layer-wise
136         10    0.1000  3.694336  layer-wise
137         10    1.0000  2.295197  layer-wise
138         10   10.0000  1.339177  layer-wise
139         10  100.0000  0.541738  layer-wise

[140 rows x 4 columns]

In [65]:
cpr_len_df.to_csv("./results/bits_lenet_withbias_b{}_lr{}_{}_gaussian.csv".format(batch_size, lr, dataset), index=False)